<a href="https://colab.research.google.com/github/swilsonmfc/timeseries/blob/master/GreyKite.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# GreyKite

![](https://engineering.linkedin.com/content/dam/engineering/site-assets/images/blog/posts/2021/05/greykite1.png)

# Intro
* https://linkedin.github.io/greykite
* https://arxiv.org/abs/2105.01098

![](https://engineering.linkedin.com/content/dam/engineering/site-assets/images/blog/posts/2021/05/greykite2.png)

# Install

In [1]:
!pip install greykite

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 22.5 MB 75.0 MB/s 
     |████████████████████████████████| 97 kB 1.4 MB/s 
     |████████████████████████████████| 211 kB 48.3 MB/s 
     |████████████████████████████████| 1.4 MB 45.7 MB/s 
     |████████████████████████████████| 297 kB 43.0 MB/s 
     |████████████████████████████████| 9.9 MB 28.6 MB/s 
     |████████████████████████████████| 9.8 MB 43.3 MB/s 
     |████████████████████████████████| 11.2 MB 35.9 MB/s 
     |████████████████████████████████| 944 kB 38.1 MB/s 
  Attempting uninstall: pandas
    Found existing installation: pandas 1.3.5
    Uninstalling pandas-1.3.5:
      Successfully uninstalled pandas-1.3.5
  Attempting uninstall: statsmodels
    Found existing installation: statsmodels 0.10.2
    Uninstalling statsmodels-0.10.2:
      Successfully uninstalled statsmodels-0.10.2
  Attempting uninstall: pluggy
    Found existing in

# Setup

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly

from greykite.algo.changepoint.adalasso.changepoint_detector import ChangepointDetector
from greykite.algo.forecast.silverkite.constants.silverkite_holiday import SilverkiteHoliday
from greykite.algo.forecast.silverkite.constants.silverkite_seasonality import SilverkiteSeasonalityEnum
from greykite.algo.forecast.silverkite.forecast_simple_silverkite_helper import cols_interact
from greykite.common import constants as cst
from greykite.common.features.timeseries_features import build_time_features_df
from greykite.common.features.timeseries_features import convert_date_to_continuous_time
from greykite.framework.templates.autogen.forecast_config import EvaluationPeriodParam
from greykite.framework.templates.autogen.forecast_config import ForecastConfig
from greykite.framework.templates.autogen.forecast_config import MetadataParam
from greykite.framework.templates.autogen.forecast_config import ModelComponentsParam
from greykite.framework.templates.forecaster import Forecaster
from greykite.framework.templates.model_templates import ModelTemplateEnum
from greykite.framework.utils.result_summary import summarize_grid_search_results

# Data

In [3]:
!wget -O data.zip https://archive.ics.uci.edu/ml/machine-learning-databases/00360/AirQualityUCI.zip
!unzip -o data.zip

--2022-08-04 13:15:37--  https://archive.ics.uci.edu/ml/machine-learning-databases/00360/AirQualityUCI.zip
Resolving archive.ics.uci.edu (archive.ics.uci.edu)... 128.195.10.252
Connecting to archive.ics.uci.edu (archive.ics.uci.edu)|128.195.10.252|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1543989 (1.5M) [application/x-httpd-php]
Saving to: ‘data.zip’

data.zip            100%[===================>]   1.47M  3.23MB/s    in 0.5s    

2022-08-04 13:15:38 (3.23 MB/s) - ‘data.zip’ saved [1543989/1543989]

Archive:  data.zip
  inflating: AirQualityUCI.csv       
  inflating: AirQualityUCI.xlsx      


In [8]:
df = pd.read_csv('AirQualityUCI.csv', sep=';', parse_dates=[['Date', 'Time']])
df

Date_Time CO(GT)  PT08.S1(CO)  NMHC(GT) C6H6(GT)  \
0     10/03/2004 18.00.00    2,6       1360.0     150.0     11,9   
1     10/03/2004 19.00.00      2       1292.0     112.0      9,4   
2     10/03/2004 20.00.00    2,2       1402.0      88.0      9,0   
3     10/03/2004 21.00.00    2,2       1376.0      80.0      9,2   
4     10/03/2004 22.00.00    1,6       1272.0      51.0      6,5   
...                   ...    ...          ...       ...      ...   
9466              nan nan    NaN          NaN       NaN      NaN   
9467              nan nan    NaN          NaN       NaN      NaN   
9468              nan nan    NaN          NaN       NaN      NaN   
9469              nan nan    NaN          NaN       NaN      NaN   
9470              nan nan    NaN          NaN       NaN      NaN   

      PT08.S2(NMHC)  NOx(GT)  PT08.S3(NOx)  NO2(GT)  PT08.S4(NO2)  \
0            1046.0    166.0        1056.0    113.0        1692.0   
1             955.0    103.0        1174.0     92.0        1559.0   
2             939.0    131.0        1140.0    114.0        1555.0   
3             948.0    172.0        1092.0    122.0        1584.0   
4             836.0    131.0        1205.0    116.0        1490.0   
...             ...      ...           ...      ...           ...   
9466            NaN      NaN           NaN      NaN           NaN   
9467            NaN      NaN           NaN      NaN           NaN   
9468            NaN      NaN           NaN      NaN           NaN   
9469            NaN      NaN           NaN      NaN           NaN   
9470            NaN      NaN           NaN      NaN           NaN   

      PT08.S5(O3)     T    RH      AH  Unnamed: 15  Unnamed: 16  
0          1268.0  13,6  48,9  0,7578          NaN          NaN  
1           972.0  13,3  47,7  0,7255          NaN          NaN  
2          1074.0  11,9  54,0  0,7502          NaN          NaN  
3          1203.0  11,0  60,0  0,7867          NaN          NaN  
4          1110.0  11,2  59,6  0,7888          NaN          NaN  
...           ...   ...   ...     ...          ...          ...  
9466          NaN   NaN   NaN     NaN          NaN          NaN  
9467          NaN   NaN   NaN     NaN          NaN          NaN  
9468          NaN   NaN   NaN     NaN          NaN          NaN  
9469          NaN   NaN   NaN     NaN          NaN          NaN  
9470          NaN   NaN   NaN     NaN          NaN          NaN  

[9471 rows x 16 columns]

## Column Processing

In [9]:
df = df.rename(columns={'PT08.S1(CO)': 'PT08S1',
                        'PT08.S2(NMHC)': 'PT08S2',
                        'PT08.S3(NOx)': 'PT08S3',
                        'PT08.S4(NO2)': 'PT08S4',
                        'PT08.S5(O3)': 'PT08S5'})

In [10]:
COLUMNS = ['Date_Time', 
           'CO(GT)', 
           'PT08S1', 
           'PT08S2', 
           'PT08S3', 
           'PT08S4', 
           'PT08S5', 
           'T', 
           'RH', 
           'AH']
df = df[COLUMNS]
df = df.dropna()

In [11]:
for col in ['CO(GT)', 'T', 'RH', 'AH']:
  df[col] = df[col].str.replace(',', '.').astype(float)

## Date Formatting

In [12]:
df['Date_Time'] = pd.to_datetime(df['Date_Time'], format='%d/%m/%Y %H.%M.00')

## Missing Values

In [13]:
df = df.replace(-200., np.NaN)
missing_df = df.copy()
df = df.ffill()

## Review

In [14]:
df

Date_Time  CO(GT)  PT08S1  PT08S2  PT08S3  PT08S4  PT08S5  \
0    2004-03-10 18:00:00     2.6  1360.0  1046.0  1056.0  1692.0  1268.0   
1    2004-03-10 19:00:00     2.0  1292.0   955.0  1174.0  1559.0   972.0   
2    2004-03-10 20:00:00     2.2  1402.0   939.0  1140.0  1555.0  1074.0   
3    2004-03-10 21:00:00     2.2  1376.0   948.0  1092.0  1584.0  1203.0   
4    2004-03-10 22:00:00     1.6  1272.0   836.0  1205.0  1490.0  1110.0   
...                  ...     ...     ...     ...     ...     ...     ...   
9352 2005-04-04 10:00:00     3.1  1314.0  1101.0   539.0  1374.0  1729.0   
9353 2005-04-04 11:00:00     2.4  1163.0  1027.0   604.0  1264.0  1269.0   
9354 2005-04-04 12:00:00     2.4  1142.0  1063.0   603.0  1241.0  1092.0   
9355 2005-04-04 13:00:00     2.1  1003.0   961.0   702.0  1041.0   770.0   
9356 2005-04-04 14:00:00     2.2  1071.0  1047.0   654.0  1129.0   816.0   

         T    RH      AH  
0     13.6  48.9  0.7578  
1     13.3  47.7  0.7255  
2     11.9  54.0  0.7502  
3     11.0  60.0  0.7867  
4     11.2  59.6  0.7888  
...    ...   ...     ...  
9352  21.9  29.3  0.7568  
9353  24.3  23.7  0.7119  
9354  26.9  18.3  0.6406  
9355  28.3  13.5  0.5139  
9356  28.5  13.1  0.5028  

[9357 rows x 10 columns]

# EDA

In [ ]:
df.describe()

CO(GT)       PT08S1       PT08S2       PT08S3       PT08S4  \
count  9357.000000  9357.000000  9357.000000  9357.000000  9357.000000   
mean      2.082195  1102.730362   942.548253   832.742225  1453.014535   
std       1.469801   219.588101   269.581368   255.709423   347.434084   
min       0.100000   647.000000   383.000000   322.000000   551.000000   
25%       1.000000   938.000000   733.000000   655.000000  1228.000000   
50%       1.700000  1062.000000   911.000000   807.000000  1460.000000   
75%       2.800000  1237.000000  1117.000000   968.000000  1677.000000   
max      11.900000  2040.000000  2214.000000  2683.000000  2775.000000   

            PT08S5            T           RH           AH  
count  9357.000000  9357.000000  9357.000000  9357.000000  
mean   1030.511916    18.317356    48.817431     1.017382  
std     410.916759     8.821883    17.354326     0.404829  
min     221.000000    -1.900000     9.200000     0.184700  
25%     726.000000    11.900000    35.400000     0.726200  
50%     964.000000    17.600000    48.900000     0.987500  
75%    1287.000000    24.300000    61.900000     1.306700  
max    2523.000000    44.600000    88.700000     2.231000

# Modeling

In [25]:
metadata = MetadataParam(
    time_col="Date_Time",  # Time column
    value_col="CO(GT)",    # Value column
    freq="H"               # Frequency
)

## Baseline

In [ ]:
forecaster_arima = Forecaster()
result_arima = forecaster_arima.run_forecast_config(
    df=df,
    config=ForecastConfig(
        model_template=ModelTemplateEnum.AUTO_ARIMA.name,
        forecast_horizon=48,  # steps ahead
        coverage=0.95,        # 95% prediction intervals
        metadata_param=metadata
    )
)

Fitting 3 folds for each of 1 candidates, totalling 3 fits


/usr/local/lib/python3.7/dist-packages/pmdarima/arima/arima.py:692: UserWarning: As of version 1.5.0 'typ' is no longer a valid arg for predict. In future versions this will raise a TypeError.
  warnings.warn("As of version 1.5.0 'typ' is no longer a valid "
/usr/local/lib/python3.7/dist-packages/pmdarima/arima/arima.py:692: UserWarning: As of version 1.5.0 'typ' is no longer a valid arg for predict. In future versions this will raise a TypeError.
  warnings.warn("As of version 1.5.0 'typ' is no longer a valid "
/usr/local/lib/python3.7/dist-packages/greykite/common/evaluation.py:154: UserWarning: 1 value(s) in y_pred were NA and are omitted in error calc.
  f"{num_removed} value(s) in {reference_array_names} were {removed_elements} and are omitted in error calc.")
/usr/local/lib/python3.7/dist-packages/greykite/common/evaluation.py:154: UserWarning: 1 value(s) in y_pred were NA and are omitted in error calc.
  f"{num_removed} value(s) in {reference_array_names} were {removed_elements}

## Prophet

In [ ]:
forecaster_prophet = Forecaster()
result_prophet = forecaster_prophet.run_forecast_config(
    df=df,
    config=ForecastConfig(
        model_template=ModelTemplateEnum.PROPHET.name,
        forecast_horizon=48,  # steps ahead
        coverage=0.95,        # 95% prediction intervals
        metadata_param=metadata
    )
)

Fitting 3 folds for each of 1 candidates, totalling 3 fits


20:58:02 - cmdstanpy - INFO - Chain [1] start processing
20:58:02 - cmdstanpy - INFO - Chain [1] done processing
20:58:10 - cmdstanpy - INFO - Chain [1] start processing
20:58:20 - cmdstanpy - INFO - Chain [1] done processing
20:58:35 - cmdstanpy - INFO - Chain [1] start processing
20:58:49 - cmdstanpy - INFO - Chain [1] done processing
20:59:05 - cmdstanpy - INFO - Chain [1] start processing
20:59:21 - cmdstanpy - INFO - Chain [1] done processing
20:59:33 - cmdstanpy - INFO - Chain [1] start processing
20:59:48 - cmdstanpy - INFO - Chain [1] done processing


## Silverkite

In [ ]:
forecaster_silverkite = Forecaster()
result_silverkite = forecaster_silverkite.run_forecast_config(
    df=df,
    config=ForecastConfig(
        model_template=ModelTemplateEnum.SILVERKITE.name,
        forecast_horizon=48,  # steps ahead
        coverage=0.95,        # 95% prediction intervals
        metadata_param=metadata
    )
)

Fitting 3 folds for each of 1 candidates, totalling 3 fits


/usr/local/lib/python3.7/dist-packages/greykite/algo/uncertainty/conditional/conf_interval.py:212: UserWarning: No slice had sufficient sample size. We fall back to the overall distribution.
  warnings.warn("No slice had sufficient sample size. We fall back to the overall distribution.")
/usr/local/lib/python3.7/dist-packages/greykite/algo/forecast/silverkite/forecast_silverkite.py:1094: UserWarning: The autoregression lags data had to be interpolated at predict time.`past_df` was either not passed to `predict_silverkite` or it was not long enough to calculate all necessery lags which is equal to `max_lag_order`=504
  "The autoregression lags data had to be interpolated at predict time."


## Forecasts

In [ ]:
forecast_arima = result_arima.forecast
fig = forecast_arima.plot()
plotly.io.show(fig)

In [ ]:
forecast_prophet = result_prophet.forecast
fig = forecast_prophet.plot()
plotly.io.show(fig)

In [ ]:
forecast_silverkite = result_silverkite.forecast
fig = forecast_silverkite.plot()
plotly.io.show(fig)

## BackTesting
* MAPE is pretty high

In [ ]:
results = [result_arima, result_prophet, result_silverkite]
testing = [pd.DataFrame(r.backtest.test_evaluation, index=['value']).T for r in results]
results_df = pd.concat(testing, axis=1)
results_df.columns = ['ARIMA', 'Prophet', 'Silverkite']
results_df

ARIMA     Prophet  \
CORR                                                  0.136424    0.506279   
R2                                                   -0.035081     0.15184   
MSE                                                   1.034969    0.848068   
RMSE                                                  1.017334    0.920906   
MAE                                                   0.647154    0.637089   
MedAE                                                 0.399659    0.475396   
MAPE                                                 56.157266    53.28674   
MedAPE                                               44.782389   41.068829   
sMAPE                                                22.936655   29.475169   
Q80                                                   0.389894    0.390984   
Q95                                                   0.423053    0.427205   
Q99                                                   0.431895    0.436863   
OutsideTolerance1p                                    0.979167         1.0   
OutsideTolerance2p                                    0.958333         1.0   
OutsideTolerance3p                                      0.9375    0.979167   
OutsideTolerance4p                                       0.875    0.979167   
OutsideTolerance5p                                    0.854167      0.9375   
Outside Tolerance (fraction)                              None        None   
R2_null_model_score                                       None        None   
Prediction Band Width (%)                           594.369226  439.729638   
Prediction Band Coverage (fraction)                   0.979167    0.958333   
Coverage: Lower Band                                  0.520833    0.354167   
Coverage: Upper Band                                  0.458333    0.604167   
Coverage Diff: Actual_Coverage - Intended_Coverage    0.029167    0.008333   

                                                    Silverkite  
CORR                                                  0.692891  
R2                                                    0.344536  
MSE                                                   0.655393  
RMSE                                                  0.809563  
MAE                                                   0.631922  
MedAE                                                 0.571785  
MAPE                                                 74.499764  
MedAPE                                               53.072802  
sMAPE                                                23.714802  
Q80                                                    0.21264  
Q95                                                    0.16098  
Q99                                                   0.147204  
OutsideTolerance1p                                         1.0  
OutsideTolerance2p                                    0.979167  
OutsideTolerance3p                                      0.9375  
OutsideTolerance4p                                    0.916667  
OutsideTolerance5p                                    0.895833  
Outside Tolerance (fraction)                              None  
R2_null_model_score                                       None  
Prediction Band Width (%)                           361.505991  
Prediction Band Coverage (fraction)                   0.979167  
Coverage: Lower Band                                      0.75  
Coverage: Upper Band                                  0.229167  
Coverage Diff: Actual_Coverage - Intended_Coverage    0.029167

# Tuning

In [26]:
results_df = pd.DataFrame(columns=['MAE', 'MAPE'])

In [33]:
tune_df = df.copy()
tune_df.loc[9309:, 'CO(GT)'] = np.NaN

## Baseline


In [45]:
model_components = ModelComponentsParam(
    autoregression = dict(autoreg_dict = None),
    seasonality = dict(
      yearly_seasonality = False,
      quarterly_seasonality = False,
      monthly_seasonality = False,
      weekly_seasonality = False,
      daily_seasonality = False,
))

forecaster = Forecaster()
result = forecaster.run_forecast_config(
    df = tune_df,
    config = ForecastConfig(
        model_template = ModelTemplateEnum.SILVERKITE.name,
        forecast_horizon = 48,  # steps ahead
        coverage = 0.95,        # 95% prediction intervals
        metadata_param = metadata,
        model_components_param = model_components
    )
)

results_df.loc['Baseline'] = [
  result.backtest.train_evaluation['MAPE'],
  result.backtest.train_evaluation['MAE']
]

/usr/local/lib/python3.7/dist-packages/greykite/common/time_properties.py:443: UserWarning: CO(GT) column of the provided TimeSeries contains null values at the end. Setting 'train_end_date' to the last timestamp with a non-null value (2005-04-02 14:00:00).
  UserWarning)


Fitting 3 folds for each of 1 candidates, totalling 3 fits


/usr/local/lib/python3.7/dist-packages/greykite/algo/uncertainty/conditional/conf_interval.py:212: UserWarning: No slice had sufficient sample size. We fall back to the overall distribution.
  warnings.warn("No slice had sufficient sample size. We fall back to the overall distribution.")


In [46]:
print(result.model[-1].summary(max_colwidth=30))

================================ Model Summary =================================

Number of observations: 9309,   Number of features: 237
Method: Ridge regression
Number of nonzero features: 237
Regularization parameter: 7.279

Residuals:
         Min           1Q       Median           3Q          Max
      -3.721      -0.6434      -0.2007       0.4685        6.753

                     Pred_col  Estimate Std. Err Pr(>)_boot sig. code                95%CI
                    Intercept     1.752  0.04685     <2e-16       ***        (1.671, 1.85)
      events_Chinese New Year    0.2854   0.1213      0.020         *    (0.04599, 0.5222)
    events_Chinese New Year-1   -0.1682   0.1166      0.164                (-0.393, 0.066)
    events_Chinese New Year-2    -0.506  0.07682     <2e-16       ***   (-0.6595, -0.3539)
    events_Chinese New Year+1    0.6232   0.1335     <2e-16       ***      (0.3388, 0.893)
    events_Chinese New Year+2     0.883   0.1296     <2e-16       ***      (0.6443, 

## Seasonality
* Support for specific custom seasonalities
* Indicate auto testing

In [38]:
model_components = ModelComponentsParam(
    autoregression = dict(autoreg_dict = None),
    seasonality = dict(auto_seasonality = True))

seasonal_config = ForecastConfig(
  model_template = ModelTemplateEnum.SILVERKITE.name,
  forecast_horizon = 48,  # steps ahead
  coverage = 0.95,        # 95% prediction intervals
  metadata_param = metadata,
  model_components_param = model_components)

forecaster = Forecaster()
result = forecaster.run_forecast_config(
  df=tune_df,
  config=seasonal_config)

results_df.loc['Seasonality'] = [
  result.backtest.train_evaluation['MAPE'],
  result.backtest.train_evaluation['MAE']
]

/usr/local/lib/python3.7/dist-packages/greykite/common/time_properties.py:443: UserWarning: CO(GT) column of the provided TimeSeries contains null values at the end. Setting 'train_end_date' to the last timestamp with a non-null value (2005-04-02 14:00:00).
  UserWarning)


Fitting 3 folds for each of 1 candidates, totalling 3 fits


/usr/local/lib/python3.7/dist-packages/greykite/algo/uncertainty/conditional/conf_interval.py:212: UserWarning: No slice had sufficient sample size. We fall back to the overall distribution.
  warnings.warn("No slice had sufficient sample size. We fall back to the overall distribution.")


In [39]:
print(result.model[-1].summary(max_colwidth=30))

================================ Model Summary =================================

Number of observations: 9309,   Number of features: 491
Method: Ridge regression
Number of nonzero features: 491
Regularization parameter: 78.8

Residuals:
         Min           1Q       Median           3Q          Max
      -3.488      -0.6337      -0.1316       0.4568         7.03

                     Pred_col   Estimate Std. Err Pr(>)_boot sig. code                  95%CI
                    Intercept      4.052    0.234     <2e-16       ***         (3.547, 4.498)
      events_Chinese New Year     0.2755   0.0462     <2e-16       ***        (0.1786, 0.361)
    events_Chinese New Year-1   -0.03224  0.03503      0.338              (-0.09701, 0.04053)
    events_Chinese New Year-2    -0.1485  0.03002     <2e-16       ***    (-0.2068, -0.08865)
    events_Chinese New Year+1     0.5376  0.05203     <2e-16       ***       (0.4211, 0.6257)
    events_Chinese New Year+2     0.6536   0.0624     <2e-16       

## Regressors

In [41]:
model_components = ModelComponentsParam(
    seasonality= dict(auto_seasonality = True),
    autoregression=dict(autoreg_dict = None),
    regressors=dict(regressor_cols = ['PT08S1']))

regressor_config = ForecastConfig(
  model_template=ModelTemplateEnum.SILVERKITE.name,
  forecast_horizon = 48,  # steps ahead
  coverage = 0.95,        # 95% prediction intervals
  metadata_param=metadata,
  model_components_param=model_components)

forecaster = Forecaster()
result = forecaster.run_forecast_config(
  df = tune_df,
  config = regressor_config)

results_df.loc['Regressors'] = [
  result.backtest.train_evaluation['MAPE'],
  result.backtest.train_evaluation['MAE']
]

/usr/local/lib/python3.7/dist-packages/greykite/common/time_properties.py:443: UserWarning: CO(GT) column of the provided TimeSeries contains null values at the end. Setting 'train_end_date' to the last timestamp with a non-null value (2005-04-02 14:00:00).
  UserWarning)


Fitting 3 folds for each of 1 candidates, totalling 3 fits


/usr/local/lib/python3.7/dist-packages/greykite/algo/uncertainty/conditional/conf_interval.py:212: UserWarning: No slice had sufficient sample size. We fall back to the overall distribution.
  warnings.warn("No slice had sufficient sample size. We fall back to the overall distribution.")


In [42]:
print(result.model[-1].summary(max_colwidth=30))

================================ Model Summary =================================

Number of observations: 9309,   Number of features: 492
Method: Ridge regression
Number of nonzero features: 492
Regularization parameter: 35.62

Residuals:
         Min           1Q       Median           3Q          Max
      -3.727      -0.3912       -0.063       0.3106          5.0

                     Pred_col   Estimate Std. Err Pr(>)_boot sig. code                 95%CI
                    Intercept      1.668   0.2335     <2e-16       ***         (1.25, 2.169)
      events_Chinese New Year     0.7315  0.07778     <2e-16       ***      (0.5704, 0.8692)
    events_Chinese New Year-1    0.05913  0.06637      0.384              (-0.05588, 0.1987)
    events_Chinese New Year-2   -0.08229  0.04009      0.046         *   (-0.1709, -0.01043)
    events_Chinese New Year+1     0.6034  0.06187     <2e-16       ***       (0.489, 0.7153)
    events_Chinese New Year+2      0.321  0.06468     <2e-16       ***  

## Auto-Regression

In [48]:
model_components = ModelComponentsParam(
    seasonality = dict(auto_seasonality = True),
    autoregression = dict(autoreg_dict='auto'),
    regressors = dict(regressor_cols = ['PT08S1']))

regressor_config = ForecastConfig(
  model_template = ModelTemplateEnum.SILVERKITE.name,
  forecast_horizon = 48,  # steps ahead
  coverage = 0.95,        # 95% prediction intervals
  metadata_param = metadata,
  model_components_param = model_components)

forecaster = Forecaster()
result = forecaster.run_forecast_config(
  df = tune_df,
  config = regressor_config)

results_df.loc['Auto-Regression'] = [
  result.backtest.train_evaluation['MAPE'],
  result.backtest.train_evaluation['MAE']
]

/usr/local/lib/python3.7/dist-packages/greykite/common/time_properties.py:443: UserWarning: CO(GT) column of the provided TimeSeries contains null values at the end. Setting 'train_end_date' to the last timestamp with a non-null value (2005-04-02 14:00:00).
  UserWarning)


Fitting 3 folds for each of 1 candidates, totalling 3 fits


/usr/local/lib/python3.7/dist-packages/greykite/algo/uncertainty/conditional/conf_interval.py:212: UserWarning: No slice had sufficient sample size. We fall back to the overall distribution.
  warnings.warn("No slice had sufficient sample size. We fall back to the overall distribution.")
/usr/local/lib/python3.7/dist-packages/greykite/algo/forecast/silverkite/forecast_silverkite.py:1094: UserWarning: The autoregression lags data had to be interpolated at predict time.`past_df` was either not passed to `predict_silverkite` or it was not long enough to calculate all necessery lags which is equal to `max_lag_order`=504
  "The autoregression lags data had to be interpolated at predict time."


In [49]:
print(result.model[-1].summary(max_colwidth=30))

================================ Model Summary =================================

Number of observations: 9309,   Number of features: 498
Method: Ridge regression
Number of nonzero features: 498
Regularization parameter: 35.62

Residuals:
         Min           1Q       Median           3Q          Max
      -3.597      -0.3959      -0.0681       0.3234        5.129

                     Pred_col   Estimate Std. Err Pr(>)_boot sig. code                  95%CI
                    Intercept      1.348   0.2629     <2e-16       ***        (0.8332, 1.833)
      events_Chinese New Year     0.7265  0.08167     <2e-16       ***        (0.5491, 0.866)
    events_Chinese New Year-1   0.009833  0.06265      0.902                (-0.1018, 0.1381)
    events_Chinese New Year-2    -0.1706  0.03735     <2e-16       ***    (-0.2388, -0.09422)
    events_Chinese New Year+1     0.6055  0.06588     <2e-16       ***       (0.4725, 0.7295)
    events_Chinese New Year+2     0.2534  0.06982     <2e-16      

In [50]:
forecast = result.forecast
fig = forecast.plot()
plotly.io.show(fig)

In [51]:
fig = result.backtest.plot_components()
plotly.io.show(fig)

## Trend

In [52]:
changepoints = dict(
    changepoints_dict = dict(
      method = 'auto',
      regularization_strength = 0.1,
      resample_freq = "7D",
      potential_changepoint_distance = "7D",
      no_changepoint_proportion_from_end = 0.3,
    )
)

model_components = ModelComponentsParam(
    seasonality = dict(auto_seasonality = True),
    autoregression = dict(autoreg_dict='auto'),
    regressors = dict(regressor_cols = ['PT08S1']),
    changepoints = changepoints)

trend_config = ForecastConfig(
  model_template=ModelTemplateEnum.SILVERKITE.name,
  forecast_horizon = 48,  # steps ahead
  coverage = 0.95,        # 95% prediction intervals
  metadata_param = metadata,
  model_components_param = model_components)

forecaster = Forecaster()
result = forecaster.run_forecast_config(
  df=tune_df,
  config=trend_config)

results_df.loc['Changepoints'] = [
  result.backtest.train_evaluation['MAPE'],
  result.backtest.train_evaluation['MAE']
]

/usr/local/lib/python3.7/dist-packages/greykite/common/time_properties.py:443: UserWarning:

CO(GT) column of the provided TimeSeries contains null values at the end. Setting 'train_end_date' to the last timestamp with a non-null value (2005-04-02 14:00:00).



Fitting 3 folds for each of 1 candidates, totalling 3 fits


/usr/local/lib/python3.7/dist-packages/greykite/algo/uncertainty/conditional/conf_interval.py:212: UserWarning:

No slice had sufficient sample size. We fall back to the overall distribution.

/usr/local/lib/python3.7/dist-packages/greykite/algo/forecast/silverkite/forecast_silverkite.py:1094: UserWarning:

The autoregression lags data had to be interpolated at predict time.`past_df` was either not passed to `predict_silverkite` or it was not long enough to calculate all necessery lags which is equal to `max_lag_order`=504



## Comparison

In [53]:
results_df

MAE      MAPE
Baseline         79.451316  0.814045
Seasonality      69.900401  0.782519
Regressors       53.224732  0.563258
Auto-Regression  51.541649  0.557539
Changepoints     53.878713  0.583778

# Misc

## Changepoints

In [ ]:
model = ChangepointDetector()
 
result = model.find_trend_changepoints(
  df=df,  
  time_col='Date_Time',  
  value_col='CO(GT)',    
  regularization_strength=0.25,  # between 0.0 and 1.0, larger values indicates fewer changepoints
  resample_freq='7D',            # data aggregation frequency, eliminate small fluctuation/seasonality
  potential_changepoint_n=10,    # the number of potential changepoints
  no_changepoint_distance_from_end='30D')  # the proportion of data from end where changepoints are not allowed
 
fig = model.plot(
  observation=True,
  trend_estimate=False,
  trend_change=True,
  adaptive_lasso_estimate=True,
  plot=False)

plotly.io.show(fig)

## Other Capabilities
* Custom Uncertainty Intervals
* Holidays & Events
* Growth (Dampening)
* Benchmarking

https://github.com/linkedin/greykite/pulse